In [2]:
from manim import *
config.media_embed = True
config.media_width = "50%"
config.verbosity = "WARNING"

In [3]:
%%manim -v WARNING -qh --disable_caching Wave
import numpy as np
from random import *


class Wave(Scene):
    def construct(self):

        maze_string = """
#######################################################
#  #################            ##                    #
# ##################           ####                   #
# #################            ####                   #
#  ###############             #####               # ##
#      #########               #####               ####
#         ###                  ######            ######
#          ###            ##   #####    ###       #####
#          ####      ########   ####  #####        ## #
#          #####   ##########   ###  ########       # #
#         #####   ###########        ########         #
#         ####   ###########        ##########        #
#        ##      ###########        ##########        #
#      ####     ############      #############       #
#    ######     ############     #############        #
# #########  ## ###########     #########    #        #
# ############### #########     #######               #
# ###############   ######      ######                #
# ###############    #####       ####                 #
#   #############      #                ##            #
#     #  #######                       ########### ####
#          ###         #              #################
# ##                  ####            #################
#####                ######          ##################
######                ######         ##################
# ###      ###        #######  ###   ###############  #
#         ####         ############   ####  #######   #
#        #####          ############          ###     #
#         ###            ##########                   #
#######################################################
"""

        maze = []  # 2D array of squares like we see it
        maze_bool = []  # 2D array of true/false values
        all_squares = VGroup()

        for row in maze_string.strip().split("\n"):
            maze.append([])
            maze_bool.append([])
            for char in row:
                maze[-1].append(
                    Square(
                        color=WHITE if char == " " else BLACK,
                        fill_opacity=1
                    ).scale(0.1)
                )
                maze_bool[-1].append(char == " ")
                all_squares.add(maze[-1][-1])
        
        rows = len(maze)
        cols = len(maze[0])
        
        self.play(FadeIn(all_squares.arrange_in_grid(rows, cols, buff=0.05)))

        x, y = 1, 1
        distances = {(x, y): 0}
        stack = [(x, y, 0)]

        while stack:
            x, y, d = stack.pop(0)
            for dx, dy in [(1, 0), (-1, 0), (0, 1), (0, -1)]:
                if x + dx < 0 or x + dx >= cols or y + dy < 0 or y + dy >= rows:
                    continue
                if maze_bool[y + dy][x + dx] and (x + dx, y + dy) not in distances:
                    distances[(x + dx, y + dy)] = d + 1
                    stack.append((x + dx, y + dy, d + 1))
        
        max_distance = max(distances.values())
        colors = ["#ef476f", "#ffd166", "#06d6a0", "#118ab2"]
        all_colors = color_gradient(colors, max_distance + 1)

        group = []
        for c in range(max_distance + 1):
            group.append(
                AnimationGroup(
                    *[
                        maze[y][x].animate.set_color(color=all_colors[c])
                        for x, y in distances.keys()
                        if distances[(x, y)] == c
                    ]
                )
            )
            
        self.play(AnimationGroup(*group, lag_ratio=0.01))
    

    



Manim Community v0.18.1

In [106]:
%%manim -v WARNING -qh --disable_caching Hilbert

class Hilbert(Scene):

    def construct(self):
        def unit_hilbert_curve(points):
            return VMobject(color=WHITE).set_points_as_corners(points)
        
        points = [LEFT+DOWN, LEFT+UP, RIGHT+UP, RIGHT+DOWN]
        hilbert = unit_hilbert_curve(points).scale(3)
        hilbert_points = list(hilbert.get_start_anchors()) + [hilbert.get_end_anchors()[-1]]
        self.play(Create(hilbert))

        dl = unit_hilbert_curve(points)
        ul = unit_hilbert_curve(points)
        ur = unit_hilbert_curve(points)
        dr = unit_hilbert_curve(points)
        
        self.play(Create(ur), Create(ul), Create(dr), Create(dl))

        self.play(
            AnimationGroup(
                dl.animate.align_to(hilbert, hilbert_points[0]).set_color(DARK_GRAY).rotate(-PI/2),
                ul.animate.align_to(hilbert, hilbert_points[1]).set_color(DARK_GRAY),
                ur.animate.align_to(hilbert, hilbert_points[2]).set_color(DARK_GRAY), 
                dr.animate.align_to(hilbert, hilbert_points[3]).set_color(DARK_GRAY).rotate(PI/2),
            ),
            FadeOut(hilbert)
        )
        hilbert_points = [dl.get_end_anchors()[-1]] + list(dl.get_start_anchors())[::-1] + list(ul.get_start_anchors()) + [ul.get_end_anchors()[-1]] + list(ur.get_start_anchors()) + [ur.get_end_anchors()[-1]] + [dr.get_end_anchors()[-1]] + list(dr.get_start_anchors())[::-1]

        new_hilbert = unit_hilbert_curve(hilbert_points)
        self.play(Create(new_hilbert))


        

Manim Community v0.18.1

In [ ]:
%%manim -v WARNING -qh --disable_caching BasicAnimation 
import numpy as np

class BasicAnimation(Scene):
    def construct(self):
        self.next_section("Rate functions")
        polys = VGroup(
            *[
                RegularPolygon(5, radius=1, fill_opacity=0.5, color=WHITE) for _ in range(5)
            ]
        ).arrange(RIGHT)
        self.play(DrawBorderThenFill(polys), run_time=2)
        self.play(
            Rotate(polys[0], angle=PI, rate_func=lambda t: t),
            Rotate(polys[1], angle=PI, rate_func=lambda t: np.sin(t * PI)),
            Rotate(polys[2], angle=PI, rate_func=smooth),
            Rotate(polys[3], angle=PI, rate_func=there_and_back),
            Rotate(polys[4], angle=PI, rate_func=lambda t: 1 - abs(1 - 2 * t)),
            run_time=2
        )
        self.wait(1)
        


In [ ]:
#more rate functions on https://easings.net/
%%manim -v WARNING -qh --disable_caching RateFunctions2

class RateFunctions2(Scene):
    def construct(self):
        lines = VGroup(
            Line(LEFT*3, RIGHT).set_color(RED),
            Line(LEFT*3, RIGHT).set_color(GREEN),
            Line(LEFT*3, RIGHT).set_color(BLUE),
            Line(LEFT*3, RIGHT).set_color(YELLOW)
        )
        lines.arrange(DOWN, buff=1)
        lines.shift(LEFT)

        labels = VGroup(
            Tex(r"smooth (default)"),
            Tex(r"linear"),
            Tex(r"there\_and\_back"),
            Tex(r"rush\_into")
        )
        for label, line in zip(labels, lines):
            label.next_to(line, RIGHT, buff=1)

        dots = VGroup(
            Dot(color=RED),
            Dot(color=GREEN),
            Dot(color=BLUE),
            Dot(color=YELLOW)
        )
        for dot, line in zip(dots, lines):
            dot.move_to(line.point_from_proportion(0))

        self.play(Create(lines), FadeIn(labels))
        self.play(FadeIn(dots))
        group =[]
        for dot, line, rate_functions in zip(dots, lines, [smooth, linear, there_and_back, rush_into]):
            group.append(MoveAlongPath(dot, line, rate_func=rate_functions))

        self.play(AnimationGroup(*group, lag_ratio=0, run_time=3))

Manim Community v0.18.1

In [125]:
%%manim -v WARNING -qh --disable_caching TargetUsage 
import numpy as np

class TargetUsage(Scene):
    def construct(self):
        c = Circle()
        self.play(Create(c))
        c.generate_target()
        c.target.shift(LEFT)
        c.target.scale(2)
        self.play(MoveToTarget(c))

Manim Community v0.18.1

In [127]:
%%manim -v WARNING -qh --disable_caching CustomAnimation
import numpy as np

class CustomAnimation(Scene):
    def construct(self):
        def spiral_out(mobj, t): # t is in [0, 1] and t is a completion ratio
            radius = 4 * t
            angle = 2 * PI * t * 2
            mobj.move_to(radius * np.array([np.cos(angle), np.sin(angle), 0]))
            color = interpolate_color(RED, BLUE, t)
            mobj.set_color(color)
        
        c = Circle()
        self.play(Create(c))
        self.play(UpdateFromAlphaFunc(c, spiral_out), run_time=2)

Manim Community v0.18.1

In [133]:
%%manim -v WARNING -qh --disable_caching CustomAnimation
import numpy as np

class Disperse(Animation):
    def __init__(self, mobject, dot_radius=0.05, dot_number=100, **kwargs):
        super().__init__(mobject, **kwargs)
        self.dot_radius = dot_radius
        self.dot_number = dot_number
    
    def begin(self):
        dots = VGroup(
            *[
                Dot(radius=self.dot_radius).move_to(self.mobject.point_from_proportion(p))
                for p in np.linspace(0, 1, self.dot_number)
            ]
        )
        for dot in dots:
            dot.initial_position = dot.get_center()
            dot.shift_vector = (dot.get_center() - self.mobject.get_center())
        dots.set_oppacity(0)
        self.mobject.add(dots)
        self.dots = dots
        super().begin()

    def clean_up_from_scene(self, scene: "Scene") -> None:
        super().clean_up_from_scene(scene)
        self.mobject.remove(self.dots)

    def interpolate_mobject(self, alpha: float) -> None:
        if alpha <= 0.5:
            self.mobject.set_opacity(1 - 2 * alpha, family=False)
            self.dots.set_opacity(2 * alpha)
        else:
            self.mobject.set_opacity(0)
            self.dots.set_opacity(2*(1-alpha))
            for dot in self.dots:
                dot.move_to(dot.initial_position + 2*(alpha-0.5) * dot.shift_vector)

class CustomAnimation(Scene):
    def construct(self):
        c = Circle(color=WHITE, fill_opacity=1).scale(2)
        self.play(Write(c))
        self.play(Disperse(c, dot_number=200), run_time=2)

Manim Community v0.18.1

<string>:19: DeprecationWarning: This method is not guaranteed to stay around. Please prefer setting the attribute normally or with Mobject.set().


In [ ]:
%%manim -v WARNING -qh --disable_caching GraohExample 
import numpy as np

class GraohExample(Scene):
    def construct(self):
        # the graph class expects a list of vertices and edges
        vertices = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]
        edges = [(1, 2), (2, 3), (3, 4), (2, 4), (2, 5), (6, 5),
                 (1, 7), (5, 7), (2, 8), (1, 9), (10, 8), (5, 11)]

        # we're using the layout_config's seed parameter to deterministically set the
        # vertex positions (it is otherwise set randomly)
        g = Graph(vertices, edges, layout_config={"seed": 0}).scale(1)
        g_ram = Graph(vertices, edges).scale(1)
        g_ram_2 = Graph(vertices, edges).scale(1)
        self.play(Create(VGroup(g, g_ram, g_ram_2).arrange(RIGHT)), run_time=2)
        self.wait(1)

        # the graph contains updaters that align edges with their vertices
        self.play(g.vertices[6].animate.shift((LEFT + DOWN) * 0.5))

        self.remove(*self.mobjects)
        # the graphs can also contain labels and be organized into specific layouts
        # (see the Graph class documentation for the list of all possible layouts)
        h = Graph(vertices, edges, labels=True, layout="circular")

        self.play(Write(h))
        self.play(FadeOut(h))

        self.play(Create(g))

        # color the vertex 5 and all of its neighbours
        v = 5
        self.play(
            Flash(g.vertices[v], color=RED, flash_radius=0.5),
            g.vertices[v].animate.set_color(RED),
            *[g.edges[e].animate.set_color(RED) for e in g.edges if v in e],
        )


Manim Community v0.18.1

In [162]:
%%manim -v WARNING -qh --disable_caching ExoticGraph 
import numpy as np
from random import uniform, randint, seed

class ExoticGraph(Scene):
    def construct(self):
        seed(0xDEADBEEF)
        vertices = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]
        edges = [(1, 2), (2, 3), (3, 4), (2, 4), (2, 5), (6, 5),
                    (1, 7), (5, 7), (2, 8), (1, 9), (10, 8), (5, 11)]
        
        def RandomStar():
            """Create a pretty random star."""
            return Star(
                randint(5, 7),
                fill_opacity=1,
                outer_radius=0.1,
                color=WHITE).rotate(uniform(0, 2 * PI))

        def RandomSkyLine(u, v, z_index=None):
            """Create a pretty random sky line. The z_index is necessary, since it is
            passed by the graph constructor to edges so they're behind vertices."""
            return DashedLine(u, v, dash_length=uniform(0.03, 0.07), z_index=z_index)

        g = Graph(vertices, edges,
            layout_config={"seed": 0},
            vertex_type=RandomStar,
            edge_type=RandomSkyLine,
        ).scale(2).rotate(-PI / 2)

        self.play(Write(g))

        self.play(FadeOut(g))

        

Manim Community v0.18.1

In [163]:
%%manim -v WARNING -qh --disable_caching GraphGenerationExample
from random import *
import networkx as nx


class GraphGenerationExample(Scene):
    def construct(self):
        seed(0xDEADBEEF)

        n = 12     # number of vertices
        p = 3 / n  # probability that there is an edge between a pair

        # generate until our graph is not connected (so it looks nicer)
        graph = None
        while graph is None or not nx.is_connected(graph):
            graph = nx.generators.random_graphs.gnp_random_graph(n, p)

        g = Graph.from_networkx(graph, layout_config={"seed": 0}).scale(2.2).rotate(-PI / 2)

        self.play(Write(g))

Manim Community v0.18.1

In [ ]:
%%manim -v WARNING -qh --disable_caching MovingCameraExample

class MovingCameraExample(MovingCameraScene):
    def construct(self):
        square = Square()

        self.play(Write(square))

        self.camera.frame.save_state()

        # zoom for the square to fill in the entire view (+ a bit of space)
        self.play(self.camera.frame.animate.set_height(square.height * 1.5))

        circle = Circle().next_to(square, LEFT)
        self.play(
            AnimationGroup(
                self.camera.frame.animate.move_to(circle),
                Write(circle),
                lag_ratio=0.5
            )
        )

        # zoom out (increasing frame size covers more of the screen)
        self.play(self.camera.frame.animate.scale(1.3))

        triangle = Triangle().next_to(square, RIGHT)

        # move the camera again
        self.play(
            AnimationGroup(
                self.camera.frame.animate.move_to(triangle),
                Write(triangle),
                lag_ratio=0.5,
            )
        )

        self.wait(0.5)

        self.play(self.camera.frame.animate.restore())




Manim Community v0.18.1

In [175]:
%%manim -v WARNING -qh --disable_caching CameraBackgroundChanging

class CameraBackgroundChanging(MovingCameraScene):
    def construct(self):
        self.camera.background_color = WHITE
        self.camera.frame.scale(0.6)
        square = Square(color=BLACK)
        self.play(Create(square))
        self.play(self.camera.frame.animate.scale(2))

Manim Community v0.18.1

In [183]:
%%manim -v WARNING -qh --disable_caching DotMovingAlongCircle

class DotMovingAlongCircle(MovingCameraScene):
    def construct(self):
        dot = Dot(radius=0.2, color=RED)
        circle_path = Circle(radius=2, color=WHITE)
        dot.move_to(circle_path.point_from_proportion(0))
        self.play(Create(circle_path), Create(dot))

        self.camera.frame.save_state()
        self.play(self.camera.frame.animate.move_to(dot).scale(0.2))

        # define a updater for camera frame
        def update_frame(frame):
            frame.move_to(dot)

        self.camera.frame.add_updater(update_frame)
        self.play(MoveAlongPath(dot, circle_path), run_time=4, rate_func=there_and_back)


Manim Community v0.18.1

In [5]:
%%manim -v WARNING -qh --disable_caching DFSExample
from random import randint, sample, seed

class DFSExample(Scene):
    def construct(self):
        # seed(0xDEADBEEF)
        
        ver = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]

        def generate_edges(vertices):
            edges = []
            for v in vertices+sample(vertices, 3):
                w = randint(1, 11)
                while w == v or (v, w) in edges or (w, v) in edges:
                    w = randint(1, 11)
                edges.append((v, w))
            return edges
        
        edges = generate_edges(ver)
        print(edges)

        g = Graph(ver, edges, layout_config={"seed": 0}).scale(1)
        self.play(Write(g))

        print(g.vertices, g.edges)
        visited = set()
        dot = Dot(g.vertices[1].get_center(), color=BLUE)
        
        def dfs(node, graph, visited, back_path=None, pre_node=None):
            if back_path is None:
                back_path = []
            if node not in visited:
                visited.add(node)
                
                # Highlight the current node
                self.play(
                    Flash(g.vertices[node], color=RED, flash_radius=0.1),
                    g.vertices[node].animate.set_color(RED)
                )
                if not pre_node:
                    self.play(Create(dot))
                    back_path.append(node)
                    print("Back path:", back_path)
                else:
                    start_pos = g.vertices[pre_node].get_center()
                    end_pos = g.vertices[node].get_center()
                    self.play(MoveAlongPath(dot, Line(start_pos, end_pos), run_time=1))
                    back_path.append(node)
                    print("Back path:", back_path)
                # If we've visited all nodes, end
                if len(visited) == len(graph):
                    return back_path

                # Explore neighbors
                # n is an edge in g.edges. We check if node is part of that edge.
                neibours_animation = []
                for n in [e for e in g.edges if node in e]:
                    if n[0] in visited and n[1] in visited:
                        pass
                    neibours_animation.append(g.edges[n].animate.set_color(BLUE))
                self.play(*neibours_animation)

                neighbors = [n[1] if n[0] == node else n[0] for n in g.edges if node in n]
                if all([n in visited for n in neighbors]):
                    start_pos = g.vertices[node].get_center()
                    end_pos = g.vertices[pre_node].get_center()
                    self.play(MoveAlongPath(dot, Line(start_pos, end_pos), run_time=1))
                    back_path.pop()
                    print("Back path:", back_path)

                for n in [e for e in g.edges if node in e]:
                    # Determine the neighbor node from the edge
                    neighbor = n[1] if n[0] == node else n[0]
                    pre_node = node
                    back_path = dfs(neighbor, graph, visited, back_path, pre_node)
            
            return back_path

        graph = [v for v in g.vertices]
        print("Graph:", graph)

        # Start DFS from node 1
        bp = dfs(1, graph, visited)
        print("Back path:", bp)

        # Reverse back_path once
        reversed_bp = bp[::-1]

        # Iterate over consecutive pairs using zip
        for start_node, end_node in zip(reversed_bp, reversed_bp[1:]):
            self.play(
                MoveAlongPath(
                    dot, 
                    Line(g.vertices[start_node].get_center(), g.vertices[end_node].get_center()), 
                    run_time=1
                )
            )




Manim Community v0.18.1

[(1, 11), (2, 9), (3, 8), (4, 1), (5, 10), (6, 4), (7, 1), (8, 6), (9, 1), (10, 8), (11, 2), (9, 11), (11, 7), (10, 6)]


{1: Dot, 2: Dot, 3: Dot, 4: Dot, 5: Dot, 6: Dot, 7: Dot, 8: Dot, 9: Dot, 10: Dot, 11: Dot} {(1, 11): Line, (2, 9): Line, (3, 8): Line, (4, 1): Line, (5, 10): Line, (6, 4): Line, (7, 1): Line, (8, 6): Line, (9, 1): Line, (10, 8): Line, (11, 2): Line, (9, 11): Line, (11, 7): Line, (10, 6): Line}
Graph: [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]


Back path: [1]


Back path: [1, 11]


...

Back path: [1, 11, 2, 4, 6, 8]


Back path: [1, 11, 2, 4, 6, 8, 3]


Back path: [1, 11, 2, 4, 6, 8]


Back path: [1, 11, 2, 4, 6, 8, 10]


Back path: [1, 11, 2, 4, 6, 8, 10, 5]
Back path: [1, 11, 2, 4, 6, 8, 10, 5]


In [89]:
%%manim -v WARNING -qh --disable_caching FibonacciExample

class FibonacciExample(MovingCameraScene):
    def construct(self):
        def generate_fibonacci_list(list_length):
            """A function to generate a list of Fibonacci numbers larger than 0."""
            a, b = 1, 1
            fibonacci_list = []
            for _ in range(list_length+2):
                fibonacci_list.append(a)
                a, b = b, a + b
            return fibonacci_list
        
        def label_generator(square_side_length):
            return MathTex(fr"{square_side_length}^{2}").set_color(WHITE)

        def obj_center(pre_obj_center, next_obj_center):
            return (pre_obj_center + next_obj_center) / 2
        
        list_length = 8
        fibonacci_list = generate_fibonacci_list(list_length)
        print(fibonacci_list)
        
        direction = [(LEFT,UP),(DOWN, LEFT), (RIGHT, DOWN), (UP, RIGHT)]
        squares = []
        for i in range(list_length-1):
            direction_index = i % 4
            square = Square().set(height=fibonacci_list[i]).set_color(WHITE)
            if i == 0:
                square.move_to(ORIGIN)
                label = label_generator(fibonacci_list[i]).move_to(square.get_center()).set(height=fibonacci_list[i] / 2)
                self.play(Create(square), FadeIn(label))
                self.play(
                    AnimationGroup(
                        self.camera.frame.animate.set(height = fibonacci_list[i+1] * 1.5),
                        run_time=1.5, lag_ratio=0
                    )
                )
                squares.append(square)
                pre_obj_center = square.get_center()
            else:
                square.next_to(squares[i - 1], direction[direction_index-1][0], buff=0).align_to(squares[i - 1], direction[direction_index-1][1])
                next_obj_center = square.get_center()
                label = label_generator(fibonacci_list[i]).move_to(square.get_center()).set(height=fibonacci_list[i] / 2)
                self.play(
                    AnimationGroup(
                        Create(square), 
                        FadeIn(label), 
                        self.camera.frame.animate.set(height = fibonacci_list[i+1] * 1.5).move_to(obj_center(pre_obj_center, next_obj_center)),
                        # multiple objects in camera frame animation may cause conflict, so it is better combine them into one
                        lag_ratio=0,
                        run_time = 1.5
                    )
                )
                squares.append(square)

        for i, sq in enumerate(squares):
            p = i % 4
            q = (i + 1) % 4
            if i == 0:
                dot = Dot(sq.get_vertices()[1], color=BLUE).scale(1.5)
                self.play(self.camera.frame.animate.move_to(dot).set(height=2), run_time=2)
                self.play(Create(dot))
                self.camera.frame.add_updater(lambda m: m.move_to(dot))
                pre_sq = sq
            else:
                arc = ArcBetweenPoints(pre_sq.get_vertices()[p], sq.get_vertices()[q], angle=PI/2)
                trace = TracedPath(dot.get_center)
                self.add(trace)
                self.play(
                    AnimationGroup(
                        MoveAlongPath(dot, arc, rate_func=smooth),
                        self.camera.frame.animate.set(height=sq.get_height() * 1.5),
                        lag_ratio = 0,
                        run_time = 1.5
                    )
                )
                pre_sq = sq
        self.wait()
                
                
                    

        


Manim Community v0.18.1

[1, 1, 2, 3, 5, 8, 13, 21, 34, 55]


<string>:72: DeprecationWarning: This method is not guaranteed to stay around. Please prefer getting the attribute normally.
<string>:72: DeprecationWarning: This method is not guaranteed to stay around. Please prefer getting the attribute normally.
<string>:72: DeprecationWarning: This method is not guaranteed to stay around. Please prefer getting the attribute normally.
<string>:72: DeprecationWarning: This method is not guaranteed to stay around. Please prefer getting the attribute normally.
<string>:72: DeprecationWarning: This method is not guaranteed to stay around. Please prefer getting the attribute normally.
<string>:72: DeprecationWarning: This method is not guaranteed to stay around. Please prefer getting the attribute normally.


In [2]:
%%manim -v WARNING -qh --disable_caching AllUpdaterTypes

class AllUpdaterTypes(Scene):
    def construct(self):
        red_dot = Dot(color=WHITE).shift(LEFT)
        pointer = Arrow(color=RED).next_to(red_dot, LEFT)
        pointer.add_updater( # place arrow left of dot
            lambda m: m.next_to(red_dot, LEFT)
        )

        def shifter(m, dt): # move dot 2 munits right/sec
            m.shift(2 * dt * RIGHT)
        # The updater function can take both the object being updated and
        # the time difference dt as positional arguments, like:
        # def update_object(obj, dt):
        #     pass
        red_dot.add_updater(shifter) 

        def scene_scaler(dt): # scale mobjects depending on distance to ORIGIN, scene updater is always time dependent
            for mob in self.mobjects:
                mob.set(width=2/(1+np.linalg.norm(mob.get_center())))
        
        self.add_updater(scene_scaler) # The scene updater functions are run every frame, and they are the last type of updaters to run.
        # Use mobject updaters to update mobjects. 
        self.add(pointer, red_dot)
        # should initially update the scene once, because the scene scaler will ruin the mobjects positions and require to run the
        # mobjects updaters again

        self.update_self(0) # 0 is the time difference, self.updater_self update the scene before dt
        self.wait(5)

    # running updater functions with disable_caching flag because manim can't see the changes in the updater

Manim Community v0.18.1

In [ ]:
%%manim -v WARNING -qh --disable_caching UpdaterAndAnimation

class UpdaterAndAnimation(Scene):
    def construct(self):
        red_dot = Dot(color=RED).shift(LEFT)
        rotating_square = Square()
        rotating_square.add_updater(lambda m, dt: m.rotate(PI*dt))

        def shifter(m, dt):
            m.shift(2 * dt * RIGHT)
        red_dot.add_updater(shifter)

        self.add(red_dot, rotating_square)
        self.wait(1)
        red_dot.suspend_updating()
        self.wait(1)

        self.play(
            red_dot.animate.shift(UP), # Updaters are resumed automatically after an animation
            rotating_square.animate.move_to([-2, -2, 0])
        )
        self.wait(1)

        # without time dependent updater, wait() wil produce static frame. so the updater is involving dt or you use
        # scene updater, pass self.wait(frozen_frame=False) to avoid static frame (wait but still runing updaters)

Manim Community v0.18.1

In [ ]:
%%manim -v WARNING -qh --disable_caching ValueTrackerExample

class ValueTrackerExample(Scene):
    def construct(self):
        a = ValueTracker(1) # ValueTracker is a simple class that stores a value, can smoothly change the value in animate
        ax = Axes(x_range=[-2, 2, 1], y_range=[-8.5, 8.5, 1],x_length=4, y_length=6)
        parabola = ax.plot(lambda x: x**2, color=RED)
        parabola.add_updater(
            lambda m: m.become(ax.plot(lambda x: x**2 * a.get_value(), color=RED)
            )
        )

        parabola.update()

        a_number = DecimalNumber(
            a.get_value(),
            num_decimal_places=2,
            include_sign=True,
            show_ellipsis=True
        )

        a_number.add_updater(lambda mob: mob.set_value(a.get_value()).next_to(parabola, RIGHT))

        self.add(ax, parabola, a_number)
        self.play(a.animate.set_value(2))
        self.play(a.animate.set_value(-2))
        self.play(a.animate.set_value(1))
        self.wait(1)

Manim Community v0.18.1

In [15]:
%%manim -v WARNING -qh --disable_caching BooleenExample

class BooleenExample(Scene):
    def construct(self):
        square = Square(fill_opacity=1).shift(UP + LEFT*0.5)
        circle = Circle(fill_opacity=1).shift(UP + RIGHT*0.5)
        self.add(square, circle)
        operations = [Intersection, Union, Exclusion, Difference]
        positions = [LEFT * 5, LEFT * 1.7, RIGHT * 1.7, RIGHT * 5]
        for op, pos in zip(operations, positions):
            result=op(square, circle).set_fill(color=BLUE, opacity=1)
            self.play(FadeIn(result))
            self.play(result.animate.shift(pos+DOWN * 3).scale(0.5))
            self.play(Write(Tex(op.__name__).move_to(result.get_center())))
        self.wait(1)


Manim Community v0.18.1

In [18]:
%%manim -v WARNING -qh --disable_caching GraphExamples

import numpy as np

class GraphExamples(Scene):
    def construct(self):
        axes = Axes(
            x_range=[-5, 5],
            y_range=[-3, 7],
        )
        labels = axes.get_axis_labels(x_label="x", y_label="y")
        self.add(axes, labels)

        def f1(x): # functions should be continuous, if not, draw them by parts
            return x**2
        
        def f2(x):
            return np.sin(x)

        g1 = axes.plot(f1, color=BLUE)
        g2 = axes.plot(f2, color=RED)

        self.play(Write(g1), Write(g2), run_time=2)

Manim Community v0.18.1

In [ ]:
%%manim -v WARNING -qh --disable_caching GraphExamples2

import numpy as np

class GraphExamples2(Scene):
    def construct(self):
        axes = Axes(x_range=[-10, 10], y_range=[-5, 5])
        labels = axes.get_axis_labels(x_label="x", y_label="y")

        def f1(t): # parametric functions are functions that take a parameter t and return a point (x, y)
            """Parametric function of a circle.""" 
            return (np.cos(t) * 3 - 4.5, np.sin(t) * 3)

        def f2(t):
            """Parametric function of a heart."""
            return (
                0.2 * (16 * (np.sin(t)) ** 3) + 4.5,
                0.2 * (13 * np.cos(t) - 5 * np.cos(2 * t) - 2 * np.cos(3 * t) - np.cos(4 * t)),
            )

        # the t_range parameter determines the range of the function parameter
        g1 = axes.plot_parametric_curve(f1, color=RED, t_range=[0, 2 * PI])
        g2 = axes.plot_parametric_curve(f2, color=BLUE, t_range=[-PI, PI])

        self.play(Write(axes), Write(labels))

        self.play(AnimationGroup(Write(g1), Write(g2), lag_ratio=0.5))

        self.play(Unwrite(axes), Unwrite(labels), Unwrite(g1), Unwrite(g2))

Manim Community v0.18.1

In [ ]:
%%manim -v WARNING -qh --disable_caching LineGraphExample

import numpy as np
from random import random, seed

class LineGraphExample(Scene):
    def construct(self):
        seed(0xDEADBEEF2)  # prettier input :P

        # value to graph (x, y);  np.arange(l, r, step) returns a list
        # from l (inclusive) do r (non-inclusive) with steps of size step
        x_values = np.arange(-1, 1 + 0.25, 0.25) # [-1, -0.75, -0.5, -0.25, 0, 0.25, 0.5, 0.75, 1]
        # looks like a list but it is a numpy array
        y_values = [random() for _ in x_values]

        # include axis numbers this time
        axes = Axes(
            x_range=[-1, 1, 0.25],
            y_range=[-0.1, 1, 0.25], 
            #x_axis_config={"numbers_to_include": x_values},
            #y_axis_config={"numbers_to_include": np.arange(0, 1, 0.25)},
            axis_config={"include_numbers": True, "decimal_number_config": {"num_decimal_places": 2}}
            # it seems include numbers works just same as numbers_to_include if you already defined the range
        )

        labels = axes.get_axis_labels(x_label="x", y_label="y")

        graph = axes.plot_line_graph(x_values=x_values, y_values=y_values)

        self.play(Write(axes), Write(labels))

        self.play(Write(graph), run_time=2)

        self.play(Unwrite(axes), Unwrite(labels), Unwrite(graph))

Manim Community v0.18.1

Manim Community v0.18.1

[12/17/24 11:43:39] WARNING  Disabling interactive embed as 'write_to_movie' is enabled               ]8;id=685061;file:///Users/enochdeng/opt/anaconda3/envs/learning/lib/python3.9/site-packages/manim/scene/scene.py\scene.py]8;;\:]8;id=758026;file:///Users/enochdeng/opt/anaconda3/envs/learning/lib/python3.9/site-packages/manim/scene/scene.py#1284\1284]8;;\

In [3]:
%%manim -v WARNING -qh --disable_caching Axes3DExample

class Axes3DExample(ThreeDScene):
    def construct(self):
        axes = ThreeDAxes()

        x_label = axes.get_x_axis_label(Tex("x"))
        y_label = axes.get_y_axis_label(Tex("y")).shift(UP * 1.8)

        # 3D variant of the Dot() object
        dot = Dot3D()

        # zoom out so we see the axes
        self.set_camera_orientation(zoom=0.5)

        self.play(FadeIn(axes), FadeIn(dot), FadeIn(x_label), FadeIn(y_label))

        self.wait(0.5)

        # animate the move of the camera to properly see the axes
        self.move_camera(phi=75 * DEGREES, theta=30 * DEGREES, zoom=1, run_time=1.5)

        # built-in updater which begins camera rotation
        self.begin_ambient_camera_rotation(rate=0.15)

        # one dot for each direction
        upDot = dot.copy().set_color(RED)
        rightDot = dot.copy().set_color(BLUE)
        outDot = dot.copy().set_color(GREEN)

        self.wait(1)

        self.play(
            upDot.animate.shift(UP),
            rightDot.animate.shift(RIGHT),
            outDot.animate.shift(OUT),
        )

        self.wait(2)

Manim Community v0.18.1